In [1]:
import numpy as np
import tensorflow as tf

In [75]:
# basic algorithm dev cell

#nxd
patterns = np.array([[-1,-1,1,-1,1,-1,-1,1],[-1,-1,-1,-1,-1,1,-1,-1],[-1,1,1,-1,-1,1,-1,1]])

#dxd
weights = np.dot(patterns.T,patterns)
print(weights.shape)

def update(patterns, weights):
    
    x = np.dot(weights, patterns.T)
    x = (x>=0)*1
    x = np.where(x==0, -1, x)
    #print(x)
    return x.T
#nxd
patterns = update(patterns, weights)
print(patterns.shape)


# task 3.1
x1d = [1,-1,1,-1,1,-1,-1,1]
x2d = [1,-1,-1,-1,-1,1,-1,-1]
x3d = [1,1,1,-1,1,1,-1,1]
xd = np.array([x1d,x2d,x3d])
print(xd.shape)

x1d = np.array([1,-1,1,-1,1,-1,-1,1])
x2d = np.array([1,-1,-1,-1,-1,1,-1,-1])
x3d = np.array([1,1,1,-1,1,1,-1,1])





(8, 8)
(3, 8)
(3, 8)


In [125]:
# class definition

class hopfield_network():
    
    
    
    def __init__(self, patterns):
        
        self.patterns = patterns
        self.weights = np.dot(patterns.T,patterns)
        #print(self.weights.shape)
        self.check_capacity()
    
    def check_capacity(self): 
    # checks whether input patterns are stable / fixed points
        
        x = self.update(patterns=self.patterns)
        assert (x == self.patterns).all(), """The network cannot store all these patterns! Ie patterns are not stable/fixed points!"""
    
    def update(self, patterns): 
    # learning rule
    
        x = np.dot(self.weights, patterns.T)
        x = (x>=0)*1
        x = np.where(x==0, -1, x)
        #print(x)
        return x.T
    
    def recall(self, distorted_patterns, max_iter): 
    # 1. tries to find stored patterns from distorted patterns up to max_iter times
    # 2. stops if fixed point is reached or pattern is correctly recalled
        
        x = distorted_patterns
        
        for i in range(max_iter):
            
            x_new = self.update(x)
            
            
#             if (x_new==self.patterns).all():
#                 print('Patterns recalled after {} iterations'.format(i+1))
#                 #print('Distorted Patterns:\n',x_new)
#                 #print('Stored Patterns:\n',self.patterns)
#                 break
                
            if (x_new==x).all():
                print('Fixed point reached after {} iterations'.format(i+1))
                #print('Distorted Patterns:\n',x_new)
                #print('Stored Patterns:\n',self.patterns)
                break
            
            x = x_new
        
        # returns the last found pattern - either a fixed point or an original pattern
        # compare it to the original patterns to which it is
        return x_new
            
    def attractor_search(self, max_bit_error = 3, search_iter = 100):
        # 1. changes stored patterns randomly by up to max_bit_error bits
        # 2. then tries to converge to the original stored pattern again
        # 3. keeps count of how many different convergence points there are (ie num of attractors)
        # 4. returns number of attractors
        
        convergence_points = []
        
        for j in range(search_iter):
            base_pattern_idx = np.random.choice(np.arange(self.patterns.shape[0])) # chooses one of n stored patterns to distort
            x = self.patterns[base_pattern_idx] # x var is our soon to be distorted pattern
            
            # distort pattern
            for i in range(max_bit_error):
                flip = np.random.choice([-1,1])
                loc = np.random.choice(np.arange(self.weights.shape[1]))
                x[loc] = flip
            
            
            # try to find original pattern - maybe change max_iter here if more complex patterns and datasets
            x_new = self.recall(x, max_iter = 50)
            convergence_points.append(x_new)
        
        #print('CONVERGENCE POINTS:\n',np.vstack(convergence_points))
        attractors = np.unique(np.vstack(convergence_points), axis=0)
        
        print('These are the attractors:\n',attractors)
        
        
        #return num of attractors
        return attractors.shape[0]
    
    def attractor_search2(self):
        # 1. create all possible distorted signals - d^2
        # 2. then try to recall a pattern from each
        # 3. count of how many different convergence points there are (ie num of attractors)
        
        convergence_points = []
        
        #dec to bin converter
        def tobin(x):
            return tobin(x/2) + [x%2] if x > 1 else [x]
        
        
        for i in range(np.square(self.weights.shape[0])):
            # 1. 
            x = tobin(i)
            print(x)
            x = np.zeros()
            # 2. 
            x_new = self.recall(np.array(x), max_iter=50)
            convergence_points.append(x_new)
        # 3.
        attractors = np.unique(np.vstack(convergence_points), axis=0)
        print('These are the attractors:\n',attractors)
        
        
        #return num of attractors
        return attractors.shape[0]
            
        
        
        
        #print('CONVERGENCE POINTS:\n',np.vstack(convergence_points))
        attractors = np.unique(np.vstack(convergence_points), axis=0)
        
        print('These are the attractors:\n',attractors)
        
        
        #return num of attractors
        return attractors.shape[0]
        
            
            
        
        
                
            
            
                
                
    

In [126]:
# Task 3.1

task = hopfield_network(patterns)
x_new1 = task.recall(x1d,10000) # ANSWER Q3.1a): Fixed point reached after 2 or 3 iter, with all distorted patterns converging.
x_new2 = task.recall(x2d,10000) # if you try recall all 3 simultaneously, x2d does not converge
x_new3 = task.recall(x3d,10000)
print(x_new1)
print(x_new2)
print(x_new3)
print('Original Patterns\n',patterns)

Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
[ 1  1 -1 -1  1  1  1  1]
[ 1  1  1 -1 -1 -1  1  1]
[ 1  1 -1  1  1  1  1  1]
Original Patterns
 [[-1 -1 -1  1  1  1 -1 -1]
 [-1 -1  1 -1 -1 -1  1 -1]
 [-1 -1  1  1 -1 -1 -1 -1]]


In [107]:
task.attractor_search(max_bit_error = 3, search_iter = 100000) 

Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 3 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after

Fixed point reached after 1 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 3 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 3 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 3 iterations
Fixed point reached after

Fixed point reached after 3 iterations
Fixed point reached after 1 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 3 iterations
Fixed point reached after 2 iterations
Fixed point reached after 1 iterations
Fixed point reached after 1 iterations
Fixed point reached after 3 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 1 iterations
Fixed point reached after 1 iterations
Fixed point reached after 1 iterations
Fixed point reached after 3 iterations
Fixed point reached after 2 iterations
Fixed point reached after

Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 3 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 3 iterations
Fixed point reached after 1 iterations
Fixed point reached after 1 iterations
Fixed point reached after 3 iterations
Fixed point reached after 2 iterations
Fixed point reached after 1 iterations
Fixed point reached after 3 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 1 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after

Fixed point reached after 2 iterations
Fixed point reached after 3 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 3 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 3 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after

...

Fixed point reached after 2 iterations
Fixed point reached after 3 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 1 iterations
Fixed point reached after 3 iterations
Fixed point reached after 2 iterations
Fixed point reached after 1 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 3 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 3 iterations
Fixed point reached after 3 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after

Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 3 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 3 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 3 iterations
Fixed point reached after 3 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after

Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 1 iterations
Fixed point reached after 3 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 1 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 3 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after

These are the attractors:
 [[-1 -1 -1  1 -1 -1 -1  1]
 [-1 -1 -1  1  1  1  1 -1]
 [-1 -1 -1  1  1  1  1  1]
 [-1  1 -1 -1 -1 -1 -1 -1]
 [-1  1 -1 -1 -1 -1 -1  1]
 [-1  1 -1 -1  1  1  1 -1]
 [-1  1 -1  1 -1 -1 -1  1]
 [ 1 -1  1  1 -1 -1 -1  1]
 [ 1 -1  1  1  1  1  1 -1]
 [ 1 -1  1  1  1  1  1  1]
 [ 1  1  1 -1 -1 -1 -1  1]
 [ 1  1  1 -1  1  1  1 -1]
 [ 1  1  1 -1  1  1  1  1]
 [ 1  1  1  1  1  1  1 -1]]


14

In [127]:
task.attractor_search2()

[0]


ValueError: shapes (8,8) and (1,) not aligned: 8 (dim 1) != 1 (dim 0)

In [ ]:
# ANSWER: Q3.1b) we found 14 different fixed points/attractors when we changed a pattern by up to 3 bits
# we searched 100 000 random pattern distortions (not systematic)

In [109]:
# Task 3.1c) 
# ANSWER: If we change more than half of the bits, the original patterns are not recalled.

x1d = np.array([1,1,-1,-1,1,1,1,-1])
x2d = np.array([1,1,1,-1,-1,-1,1,-1])
x3d = np.array([1,1,1,1,1,1,1,-1])

task = hopfield_network(patterns)
x_new1 = task.recall(x1d,10000) 
x_new2 = task.recall(x2d,10000)
x_new3 = task.recall(x3d,10000)
print(x_new1)
print(x_new2)
print(x_new3)
print('Original Patterns\n',patterns)

Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
Fixed point reached after 2 iterations
[ 1  1 -1 -1  1  1  1  1]
[ 1  1  1 -1 -1 -1  1  1]
[ 1  1 -1  1  1  1  1  1]
Original Patterns
 [[-1 -1 -1  1  1  1 -1 -1]
 [-1 -1  1 -1 -1 -1  1 -1]
 [-1 -1  1  1 -1 -1 -1 -1]]
